# Creazione di isocrone per la visualizzazione della distanza della rete stradale dalle colonnine elettriche

In [3]:
import os

from IPython.display import display
from ipywidgets import IntProgress

import folium
from folium.plugins import MarkerCluster

from openrouteservice import client
import overpass

import time
import pandas as pd
import geopandas as gpd
# import fiona as fn
from shapely.geometry import shape, mapping, LineString
from shapely.ops import cascaded_union, unary_union, polygonize
import shapely
import geojson

import matplotlib.pyplot as plt

import requests
import json

from zonal_stats import * # import zonal stats function from python file, get it here: https://gist.github.com/perrygeo/5667173

api_ov = overpass.API(timeout=600)

## Introduzione

Al fine di dividere la rete stradale in classi di distanza si è studiata la possibilità del calcolo delle isocrone calcolate tramite [OpenRouteService](https://openrouteservice.org/) (ORS). 

Le linee isocrone rappresentano l'insieme dei punti che dato un punto di partenza sono ad una determinata distanza percorrendo il grafo stradale. Possono quindi indicare l'area che è ad una determinata distanza da un punto di partenza.

![isocrone](figures/isocrone.png)
Un esempio di calcolo di isocrona tramite l'utilizzo dell'interfaccia web di ORS

Utilizzando le API (Application Programming Interface) di ORS è possibile fare delle chiamate ai server per ottenere lo stesso risultato mostrato nell'intefaccia web. In pyhton corrisponderebbe al codice:

```python
import requests

body = {"locations":[[9.2537405,45.4779112]],"range":[1000,2000]}

headers = {
    'Accept': 'application/json, application/geo+json, application/gpx+xml, img/png; charset=utf-8',
    'Authorization': '',
    'Content-Type': 'application/json; charset=utf-8'
}
call = requests.post('https://api.openrouteservice.org/v2/isochrones/driving-car', json=body, headers=headers)

print(call.text)
```

Tuttavia, il numero di richieste che è possibile fare al serve è limitato, per le isocrone a 500 al giorno, e al massimo 20 al minuto.

![limiti](figures/limiti_ORS.png)

Se si vogliono investigare grandi aree non è quindi possibile utilizzare il servizio online. Ma essendo il [software](https://github.com/GIScience/openrouteservice) opensource e i dati forniti da [OpenStreetMap](https://www.openstreetmap.org/) con licenza aperta è possibile installare una copia del servizio sul proprio computer.

Installazione prevede l'utilizzo di [Docker](https://www.docker.com/). Docker è una piattaforma open-source che automatizza il implementazione di applicazioni all'interno di contenitori leggeri e portabili. I contenitori sono una forma di virtualizzazione a livello di sistema operativo, che consente di eseguire applicazioni e i relativi dipendenti in ambienti isolati e indipendenti.

Verranno quindi presentati due esempi:

1. Calcolo delle isocrone in un comune utilizzando le API di ORS
2. Calcolo delle isocrone in una regione tramite l'utilizzo di API locali e l'installazione di docker

## Primo esempio: utilizzo online

Per l'utilizzo delle API è necessario registrarsi a [ORS](https://openrouteservice.org/dev/#/signup), possibile anche utilizzare il proprio account GitHub.

Dalla pagina [home](https://openrouteservice.org/dev/#/home) serve creare un token. Scegliere come tipologia `standard` e dare un nome a scelta. 

Dupplicare il file [API-example.txt](API-example.txt) e rinominarlo [API.txt](API.txt), quindi copiare il token generato nella prima riga del file.

In [2]:
# Scaricamento dei dati da OpenStreetMap
# in OSM le collonnine sono mappate come amenity=charging_station
# https://wiki.openstreetmap.org/wiki/Tag:amenity=charging%20station

name_city = "Bergamo"
query = "[out:json][timeout:60];area[\"name\"=\"" + name_city + "\"][\"admin_level\"=8]->.searchArea;node[\"amenity\"=\"charging_station\"](area.searchArea);out center;"
charging_station = api_ov.get(query, build = False)

In [3]:
# Creazione di un dizionario che contenga i dati scaricati
charging_dict = {}
for feature in charging_station["elements"]:
    facility_id = int(feature['id'])
    charging_dict[facility_id] = {
        'geometry': {"type": "Point", "coordinates": [ feature["lon"], feature["lat"] ] }
    }
print('Creato dizionario con %s colonnine' % len(charging_dict))

Creato dizionario con 29 colonnine


In [4]:
# Visualizzazione della posizione delle colonnine estratte da OpenStreetMap
map_outline = folium.Map(tiles='openstreetmap', location=([feature["lat"], feature["lon"]]), zoom_start=13)

cluster = MarkerCluster().add_to(map_outline)  

for facility_id in charging_dict:
    folium.Marker(list(reversed(charging_dict[facility_id]['geometry']['coordinates']))).add_to(cluster)

map_outline.save(os.path.join('results', "1_charging_station_overview_"+ name_city + ".html"))
map_outline

In [5]:
# Caricamento del token di ORS dal file API.txt
with open("API.txt", 'r') as file:
    api_key = file.readline()

headers = {'Accept': 'application/json, application/geo+json, application/gpx+xml, img/png; charset=utf-8', 'Authorization': api_key,'Content-Type': 'application/json; charset=utf-8'}

In [6]:
# Ciclo per calcolare le isocrone per ciascuna delle colonnine presenti nel dizionario contenente i dati scaricati da OSM

# Inizializazione variabili
i = 0
check = 0
error_counter = 0
iso_car_1 = []
iso_car_5 = []
iso_car_10 = []
list_loc = []

# Creazione di una lista con le posizioni delle colonnine
for facility_id in charging_dict.keys():
    loc = charging_dict[facility_id]['geometry']['coordinates']
    list_loc.append(loc)
l = len(list_loc)

# Ciclo
while i < l:
        # Parametri per il calcolo delle isocrone
        iso_params = {'locations': [list_loc[i]],
                'range_type': 'distance', # Selezionato il parametro distanza
                'range': [1000, 5000, 10000]  # tre differenti distanza scelte, da indicare in metri
                }
                
        call = requests.post('https://api.openrouteservice.org/v2/isochrones/driving-car', json=iso_params, headers=headers)
        request = json.loads(call.text)
        check += 1
        
        try:
                iso_car_1.append(shape(request['features'][0]['geometry']))
                iso_car_5.append(shape(request['features'][1]['geometry']))
                iso_car_10.append(shape(request['features'][2]['geometry']))
                i += 1
        except:
                print("Error for location: " + str(list_loc[i]))
                error_counter += 1
                i += 1

        # Considerato il limite di 20 richieste al minuti si attende un minuto per eseguire le successive
        if check % 19 == 0:
                print("Aspettando 60 secondi, richieste già completate: %s"  % check)
                f = IntProgress(min=0, max=60) # instantiate the bar
                display(f) # display the bar
                for t_sleep in range(0,60):
                       time.sleep(1)
                       f.value += 1
                rem = l - check
                print("Attesa terminata, richieste rimanenti: %s" % rem)

print('Sono state richieste %s isocrone' % check)
if error_counter > 0:
       print('delle quali %s non hanno fornito un risultato utile' % error_counter)

Aspettando 60 secondi, richieste già completate: 19


IntProgress(value=0, max=60)

Attesa terminata, richieste rimanenti: 10
Sono state richieste 29 isocrone


In [7]:
# Unione delle isocrone di ciascuna colonnina in un unico poligono
iso_union_car_1 = cascaded_union(iso_car_1)
iso_union_car_5 = cascaded_union(iso_car_5)
iso_union_car_10 = cascaded_union(iso_car_10)
geojson_iso_1 = shapely.to_geojson(iso_union_car_1)
geojson_iso_5 = shapely.to_geojson(iso_union_car_5)
geojson_iso_10 = shapely.to_geojson(iso_union_car_10)

# Salvataggio dei file delle isocrone
isochrones_car_filename_1 = "results/iso_union_car_1_"+ name_city + ".geojson"
isochrones_car_filename_5 = "results/iso_union_car_5_"+ name_city + ".geojson"
isochrones_car_filename_10 = "results/iso_union_car_10_"+ name_city + ".geojson"
with open(isochrones_car_filename_1, 'w') as f:
    f.write(geojson_iso_1)
with open(isochrones_car_filename_5, 'w') as f:
    f.write(geojson_iso_5)
with open(isochrones_car_filename_10, 'w') as f:
    f.write(geojson_iso_10)

/var/folders/vy/qyz4wzr16bjgg9hklcdk3wlw0000gn/T/ipykernel_13005/1105839352.py:2: ShapelyDeprecationWarning: The 'cascaded_union()' function is deprecated. Use 'unary_union()' instead.
  iso_union_car_1 = cascaded_union(iso_car_1)
/var/folders/vy/qyz4wzr16bjgg9hklcdk3wlw0000gn/T/ipykernel_13005/1105839352.py:3: ShapelyDeprecationWarning: The 'cascaded_union()' function is deprecated. Use 'unary_union()' instead.
  iso_union_car_5 = cascaded_union(iso_car_5)
/var/folders/vy/qyz4wzr16bjgg9hklcdk3wlw0000gn/T/ipykernel_13005/1105839352.py:4: ShapelyDeprecationWarning: The 'cascaded_union()' function is deprecated. Use 'unary_union()' instead.
  iso_union_car_10 = cascaded_union(iso_car_10)


In [8]:
# Visualizzazione delle isocrone

map_isochrones = folium.Map(tiles='openstreetmap', location=([feature["lat"], feature["lon"]]), zoom_start=12)

def style_function(color):  # To style isochrones
    return lambda feature: dict(color=color)

folium.GeoJson(geojson_iso_10, name="10 km", style_function = style_function('#fde725ff')).add_to(map_isochrones)
folium.GeoJson(geojson_iso_5, name="5 km",style_function = style_function('#1f968bff')).add_to(map_isochrones)
folium.GeoJson(geojson_iso_1, name="1 km",style_function = style_function('#440154ff')).add_to(map_isochrones)

cluster = MarkerCluster().add_to(map_isochrones)  

for facility_id in charging_dict:
    folium.Marker(list(reversed(charging_dict[facility_id]['geometry']['coordinates']))).add_to(cluster)

map_isochrones.save(os.path.join('results', "2_isochrones_"+ name_city + ".html"))
map_isochrones

Dopo aver calcolato e visualizzato le isocrone si procede a scaricare la rete stradale da OSM.

Sono state considerate le strade di tipologia:
- highway = motorway
- highway = trunk
- highway = primary
- highway = secondary
- highway = tertiary
- highway = motorway_link
- highway = trunk_link
- highway = primary_link
- highway = secondary_link
- highway = tertiary_link
- highway = unclassified
- highway = residential
- highway = living_street 
- highway = service 

Le cui definizioni sono disponibili nella [pagina wiki OSM](https://wiki.openstreetmap.org/wiki/IT:Key:highway).

In [9]:
query_2 = "[out:json][timeout:60];area[\"name\"=\"" + name_city + "\"][\"admin_level\"=8]->.searchArea;(way[\"highway\"=\"motorway\"](area.searchArea);way[\"highway\"=\"trunk\"](area.searchArea);way[\"highway\"=\"primary\"](area.searchArea);way[\"highway\"=\"secondary\"](area.searchArea);way[\"highway\"=\"tertiary\"](area.searchArea);way[\"highway\"=\"motorway_link\"](area.searchArea);way[\"highway\"=\"trunk_link\"](area.searchArea);way[\"highway\"=\"primary_link\"](area.searchArea);way[\"highway\"=\"secondary_link\"](area.searchArea);way[\"highway\"=\"tertiary_link\"](area.searchArea);way[\"highway\"=\"unclassified\"](area.searchArea);way[\"highway\"=\"residential\"](area.searchArea);way[\"highway\"=\"living_street\"](area.searchArea);way[\"highway\"=\"service\"](area.searchArea););out geom;"

# I dati sono estratti da OpenStreetMap e salvati in un Geodataframe
highways = api_ov.get(query_2, build = False)
strade_dict = [{
    'id': element['id'],
    'class': element['tags']['highway'],
    'geometry': LineString([(coords['lon'], coords['lat']) for coords in element['geometry']]),
} for element in highways['elements']]
strade_citta = gpd.GeoDataFrame(strade_dict)
strade_citta = strade_citta.set_crs('epsg:4326')

In [10]:
# Le isocrone sono state caricate e intersecati con la rete stradale
iso_car_1_geo = gpd.read_file("results/iso_union_car_1_"+ name_city + ".geojson", driver="GeoJSON")
iso_car_5_geo = gpd.read_file("results/iso_union_car_5_"+ name_city + ".geojson", driver="GeoJSON")
iso_car_10_geo = gpd.read_file("results/iso_union_car_10_"+ name_city + ".geojson", driver="GeoJSON")

strade_iso_car_1 = strade_citta[strade_citta.intersects(iso_car_1_geo.geometry.iloc[0])]
strade_iso_car_5 = strade_citta[strade_citta.intersects(iso_car_5_geo.geometry.iloc[0])]
strade_iso_car_10 = strade_citta[strade_citta.intersects(iso_car_10_geo.geometry.iloc[0])]

In [11]:
# I dati risultati sono visualizzati
map_strade = folium.Map(tiles='openstreetmap', location=([feature["lat"], feature["lon"]]), zoom_start=13)

folium.GeoJson(strade_citta.to_json(), name=">10 km", style_function = style_function('#F08080')).add_to(map_strade)
folium.GeoJson(strade_iso_car_10.to_json(), name="10 km", style_function = style_function('#fde725ff')).add_to(map_strade)
folium.GeoJson(strade_iso_car_5.to_json(), name="5 km",style_function = style_function('#1f968bff')).add_to(map_strade)
folium.GeoJson(strade_iso_car_1.to_json(), name="1 km",style_function = style_function('#440154ff')).add_to(map_strade)

map_strade.save(os.path.join('results', "3_strade_" + name_city + ".html"))
map_strade

In [12]:
# Le lunghezza di ciascuna classe sono calcolate e visualizzate 
l_1 = strade_iso_car_1.to_crs('epsg:32632').geometry.length.sum() # N.B. i dati sono stati riproietti in un sistema metrico
l_5 = strade_iso_car_5.to_crs('epsg:32632').geometry.length.sum() - l_1
l_10 = strade_iso_car_10.to_crs('epsg:32632').geometry.length.sum() - l_5 - l_1
l_citta = strade_citta.to_crs('epsg:32632').geometry.length.sum()
l_mag_10 = l_citta - l_10 - l_5 - l_1

data = {
    "Distanza da colonnina": ["< 1 km", "1 - 5 km", "5 - 10 km", "> 10 km"],
    "Lunghezza totale (km)": [l_1/1000, l_5/1000, l_10/1000, l_mag_10/1000],
    "Percentuale classe (%)": [l_1/l_citta*100, l_5/l_citta*100, l_10/l_citta*100, l_mag_10/l_citta*100]
}

pd.DataFrame(data)

Distanza da colonnina  Lunghezza totale (km)  Percentuale classe (%)
0                < 1 km             377.696969               72.391387
1              1 - 5 km             143.006257               27.409331
2             5 - 10 km               1.039736                0.199281
3               > 10 km               0.000000                0.000000

## Secondo esempio: utilizzo offline

L'utilizzo in locale chiede di aver installato [docker](https://www.docker.com/) e di scaricare i dati di OpenStreeMap. Il download è dispobinile sul sito [Geofabrick](https://download.geofabrik.de/). Per il test si è scaricato l'intero file dell'italia deminato `italy-latest.osm.pbf`. Disponibile dal sito di Geofabrick al [link](https://download.geofabrik.de/europe/italy.html), oppure direttamente dal [link](https://download.geofabrik.de/europe/italy-latest.osm.pbf). Il file è circa di 1,9 GB la cui velocità di download dipende dalla propria connessione. 

Copiare il file all'interno della cartella [openrouteservice-7.1.0\docker](openrouteservice-7.1.0\docker).

Nel caso si volesse utilizzare un'area differente è necessario andare ad inserire nel file [docker-compose.yml](openrouteservice-7.1.0/docker/docker-compose.yml) i riferimenti:

```yml
OSM_FILE: ./italy-latest.osm.pbf
```
```yml
- ./italy-latest.osm.pbf:/home/ors/ors-core/data/osm_file.pbf
```

Procere quindi all'avvio di docker tramite i comandi:
```bash
cd openrouteservice-7.1.0
cd docker 
mkdir conf elevation_cache graphs logs
cd logs
mkdir ors tomcat 
cd ..
docker compose up
```

Al primo avvio verrà generato il grafo stradale completo. L'operazione richie qualche minuto per essere completata, valore che varia in base al computer utilizzato.

Si può verificare lo stato di caricamento al link http://localhost:8080/ors/v2/status

Si procede poi seguendo la procedura come descritta in precedenza.

In [6]:
name_regione = "Piemonte"
query = "[out:json][timeout:60];area[\"name\"=\"" + name_regione + "\"][\"admin_level\"=4]->.searchArea;node[\"amenity\"=\"fuel\"](area.searchArea);out center;"
charging_station = api_ov.get(query, build = False)

In [7]:
charging_dict = {}
for feature in charging_station["elements"]:
    facility_id = int(feature['id'])
    charging_dict[facility_id] = {
        'geometry': {"type": "Point", "coordinates": [ feature["lon"], feature["lat"] ] }
    }
print('Creato dizionario con %s colonnine' % len(charging_dict))

Creato dizionario con 1474 colonnine


In [8]:
map_outline = folium.Map(tiles='openstreetmap', location=([feature["lat"], feature["lon"]]), zoom_start=9)

cluster = MarkerCluster().add_to(map_outline)  

for facility_id in charging_dict:
    folium.Marker(list(reversed(charging_dict[facility_id]['geometry']['coordinates']))).add_to(cluster)

map_outline.save(os.path.join('results', "1_charging_station_overview_" + name_regione + ".html"))
map_outline

In [9]:
headers = {'Accept': 'application/json, application/geo+json, application/gpx+xml, img/png; charset=utf-8','Content-Type': 'application/json; charset=utf-8'}

i = 0
check = 0
error_counter = 0

iso_car_1 = []
iso_car_5 = []
iso_car_10 = []
list_loc = []

for facility_id in charging_dict.keys():
    loc = charging_dict[facility_id]['geometry']['coordinates']
    list_loc.append(loc)
l = len(list_loc)

In [10]:
f = IntProgress(min=0, max=l) # instantiate the bar
display(f) # display the bar

while i < l:
        iso_params = {'locations': [list_loc[i]],
                'range_type': 'distance',
                'range': [5000, 5000, 10000]  # meters
                }
                
        call = requests.post('http://localhost:8080/ors/v2/isochrones/driving-car', json=iso_params, headers=headers)
        request = json.loads(call.text)
        check += 1
        
        try:
                iso_car_1.append(shape(request['features'][0]['geometry']))
                iso_car_5.append(shape(request['features'][1]['geometry']))
                iso_car_10.append(shape(request['features'][2]['geometry']))
                i += 1
        except:
                print("Errore nella colonnina in posizione: " + str(list_loc[i]))
                print("Vedi errore nella mappa: https://www.openstreetmap.org/#map=19/" + str(list_loc[i][1]) + "/" + str(list_loc[i][0]))
                error_counter += 1
                i += 1

        f.value += 1


print('Sono state richieste %s isocrone' % check)
if error_counter > 0:
       print('delle quali %s non hanno fornito un risultato utile' % error_counter)

IntProgress(value=0, max=1474)

Errore nella colonnina in posizione: [7.581473, 45.080941]
Vedi errore nella mappa: https://www.openstreetmap.org/#map=19/45.080941/7.581473
Errore nella colonnina in posizione: [8.6120152, 45.7243797]
Vedi errore nella mappa: https://www.openstreetmap.org/#map=19/45.7243797/8.6120152
Sono state richieste 1474 isocrone
delle quali 2 non hanno fornito un risultato utile


In [11]:
iso_union_car_1 = cascaded_union(iso_car_1)
iso_union_car_5 = cascaded_union(iso_car_5)
iso_union_car_10 = cascaded_union(iso_car_10)
geojson_iso_1 = shapely.to_geojson(iso_union_car_1)
geojson_iso_5 = shapely.to_geojson(iso_union_car_5)
geojson_iso_10 = shapely.to_geojson(iso_union_car_10)

isochrones_car_filename_1 = "results/iso_union_car_1_"+ name_regione + ".geojson"
isochrones_car_filename_5 = "results/iso_union_car_5_"+ name_regione + ".geojson"
isochrones_car_filename_10 = "results/iso_union_car_10_"+ name_regione + ".geojson"

# save isochrones to geojson
with open(isochrones_car_filename_1, 'w') as f:
    f.write(geojson_iso_1)
with open(isochrones_car_filename_5, 'w') as f:
    f.write(geojson_iso_5)
with open(isochrones_car_filename_10, 'w') as f:
    f.write(geojson_iso_10)

/var/folders/vy/qyz4wzr16bjgg9hklcdk3wlw0000gn/T/ipykernel_24626/4077428985.py:1: ShapelyDeprecationWarning: The 'cascaded_union()' function is deprecated. Use 'unary_union()' instead.
  iso_union_car_1 = cascaded_union(iso_car_1)
/var/folders/vy/qyz4wzr16bjgg9hklcdk3wlw0000gn/T/ipykernel_24626/4077428985.py:2: ShapelyDeprecationWarning: The 'cascaded_union()' function is deprecated. Use 'unary_union()' instead.
  iso_union_car_5 = cascaded_union(iso_car_5)
/var/folders/vy/qyz4wzr16bjgg9hklcdk3wlw0000gn/T/ipykernel_24626/4077428985.py:3: ShapelyDeprecationWarning: The 'cascaded_union()' function is deprecated. Use 'unary_union()' instead.
  iso_union_car_10 = cascaded_union(iso_car_10)


In [12]:
map_isochrones = folium.Map(tiles='openstreetmap', location=([feature["lat"], feature["lon"]]), zoom_start=9)

def style_function(color):  # To style isochrones
    return lambda feature: dict(color=color)

folium.GeoJson(geojson_iso_10, name="10 km", style_function = style_function('#fde725ff')).add_to(map_isochrones)
folium.GeoJson(geojson_iso_5, name="5 km",style_function = style_function('#1f968bff')).add_to(map_isochrones)
folium.GeoJson(geojson_iso_1, name="1 km",style_function = style_function('#440154ff')).add_to(map_isochrones)

cluster = MarkerCluster().add_to(map_isochrones)  

for facility_id in charging_dict:
    folium.Marker(list(reversed(charging_dict[facility_id]['geometry']['coordinates']))).add_to(cluster)

map_isochrones.save(os.path.join('results', "2_isochrones_" + name_regione + ".html"))
map_isochrones

In [13]:
api_ov = overpass.API(timeout=600)
query_2 = "[out:json][timeout:60];area[\"name\"=\"" + name_regione + "\"][\"admin_level\"=4]->.searchArea;(way[\"highway\"=\"motorway\"](area.searchArea);way[\"highway\"=\"trunk\"](area.searchArea);way[\"highway\"=\"primary\"](area.searchArea);way[\"highway\"=\"secondary\"](area.searchArea);way[\"highway\"=\"tertiary\"](area.searchArea);way[\"highway\"=\"motorway_link\"](area.searchArea);way[\"highway\"=\"trunk_link\"](area.searchArea);way[\"highway\"=\"primary_link\"](area.searchArea);way[\"highway\"=\"secondary_link\"](area.searchArea);way[\"highway\"=\"tertiary_link\"](area.searchArea);way[\"highway\"=\"unclassified\"](area.searchArea);way[\"highway\"=\"residential\"](area.searchArea);way[\"highway\"=\"living_street\"](area.searchArea);way[\"highway\"=\"service\"](area.searchArea););out geom;"
highways = api_ov.get(query_2, build = False)

strade_dict = [{
    'id': element['id'],
    'class': element['tags']['highway'],
    'geometry': LineString([(coords['lon'], coords['lat']) for coords in element['geometry']]),
} for element in highways['elements']]

strade_regione = gpd.GeoDataFrame(strade_dict)
strade_regione = strade_regione.set_crs('epsg:4326')
strade_regione.to_file("results/strade_"+ name_regione + ".geojson", driver="GeoJSON")  

In [14]:
iso_car_1_geo = gpd.read_file("results/iso_union_car_1_"+ name_regione + ".geojson", driver="GeoJSON")
iso_car_5_geo = gpd.read_file("results/iso_union_car_5_"+ name_regione + ".geojson", driver="GeoJSON")
iso_car_10_geo = gpd.read_file("results/iso_union_car_10_"+ name_regione + ".geojson", driver="GeoJSON")

strade_iso_car_1 = strade_regione[strade_regione.intersects(iso_car_1_geo.geometry.iloc[0])]
strade_iso_car_5 = strade_regione[strade_regione.intersects(iso_car_5_geo.geometry.iloc[0])]
strade_iso_car_10 = strade_regione[strade_regione.intersects(iso_car_10_geo.geometry.iloc[0])]

In [15]:
strade_iso_car_1.to_file("results/strade_iso_car_1_"+ name_regione + ".geojson", driver="GeoJSON")  
strade_iso_car_5.to_file("results/strade_iso_car_5_"+ name_regione + ".geojson", driver="GeoJSON")  
strade_iso_car_10.to_file("results/strade_iso_car_10_"+ name_regione + ".geojson", driver="GeoJSON")  

In [16]:
map_strade = folium.Map(tiles='openstreetmap', location=([feature["lat"], feature["lon"]]), zoom_start=9)

folium.GeoJson(strade_regione.to_json(), name=">10 km", style_function = style_function('#F08080')).add_to(map_strade)
folium.GeoJson(strade_iso_car_10.to_json(), name="10 km", style_function = style_function('#fde725ff')).add_to(map_strade)
folium.GeoJson(strade_iso_car_5.to_json(), name="5 km",style_function = style_function('#1f968bff')).add_to(map_strade)
folium.GeoJson(strade_iso_car_1.to_json(), name="1 km",style_function = style_function('#440154ff')).add_to(map_strade)

map_strade.save(os.path.join('results', "3_strade_" + name_regione + ".html"))
# I dati nella mappa sono molti e ciò rallenta molto la visualizzazione si consiglia di visualizzare la mappa tramite browser
# map_strade

In [17]:
l_1 = strade_iso_car_1.to_crs('epsg:32632').geometry.length.sum()
l_5 = strade_iso_car_5.to_crs('epsg:32632').geometry.length.sum() - l_1
l_10 = strade_iso_car_10.to_crs('epsg:32632').geometry.length.sum() - l_5 - l_1
l_regione = strade_regione.to_crs('epsg:32632').geometry.length.sum()
l_mag_10 = l_regione - l_10 - l_5 - l_1

data = {
    "Distanza da colonnina": ["< 1 km", "1 - 5 km", "5 - 10 km", "> 10 km"],
    "Lunghezza totale (km)": [l_1/1000, l_5/1000, l_10/1000, l_mag_10/1000],
    "Percentuale classe (%)": [l_1/l_regione*100, l_5/l_regione*100, l_10/l_regione*100, l_mag_10/l_regione*100]
}

pd.DataFrame(data)

Distanza da colonnina  Lunghezza totale (km)  Percentuale classe (%)
0                < 1 km           51093.405042               85.203617
1              1 - 5 km              62.981184                0.105028
2             5 - 10 km            6734.701625               11.230822
3               > 10 km            2075.151490                3.460533